In [1]:
import numpy as np
import auxiliary as au
from matplotlib import pyplot as plt
from scipy import io
import os
import sys
import h5py
import time
import random
import datetime
from optimal_interpolation import OImerge
import calendar


def box_cox_transform(data, exp=0.25):
    return (data ** exp - 1) / exp


def box_cox_recover(data, exp=0.25):
    dataout = (data * exp + 1) ** (1 / exp)
    dataout[data < -1 / exp] = 0
    return dataout


# basic settings
# y1 = int(sys.argv[3])
# y2 = int(sys.argv[4])
# year = [y1, y2]
year = [1980, 1980]

weightmode = 'RMSE'
vars = ['prcp', 'tmean', 'trange']
# "Gaussian": prcp will be transformed into normal distributions; "Actual": actual space
prcp_space = 'Actual'
hwsize = 2  # 5X5 space window used to support estimation at the center grid
lontar = np.arange(-180 + 0.05, -50, 0.1)
lattar = np.arange(85 - 0.05, 5, -0.1)

# output path of merged data
path_merge = '/Users/localuser/GMET/merge'

# path of merged reanalysis
# path_bac = '/datastore/GLOBALWATER/CommonData/EMDNA/ReanalysisCorrMerge/Reanalysis_merge'
path_bac = '/Users/localuser/GMET/merge'

# path of gridded observations
# path_obs = '/datastore/GLOBALWATER/CommonData/EMDNA/PyGMETout'
path_obs = '/Users/localuser/GMET/merge'

# mask file
# file_mask = '/datastore/GLOBALWATER/CommonData/EMDNA/DEM/NA_DEM_010deg_trim.mat'
file_mask = './DEM/NA_DEM_010deg_trim.mat'
mask = io.loadmat(file_mask)
mask = mask['DEM']
mask[~np.isnan(mask)] = 1  # 1: valid pixels
nrows, ncols = np.shape(mask)


In [2]:
for y in range(year[0], year[1] + 1):
    for m in range(1):
        print('merging date:', y * 100 + m + 1)
        filemerge = path_merge + '/OImerge_' + str(y * 100 + m + 1) + '.npz'
        if os.path.isfile(filemerge):
            print('file exists')
            continue

        date_cal_start = y * 10000 + (m + 1) * 100 + 1
        date_cal_end = y * 10000 + (m + 1) * 100 + calendar.monthrange(y, m + 1)[1]
        datestr = str(date_cal_start) + '-' + str(date_cal_end)
        oimerge_data = dict()

merging date: 198001


In [59]:
            var='prcp'
            print('variable', var)
            file_bac = path_bac + '/mergedata_' + var + '_' + str(y * 100 + m + 1) + weightmode + '.npz'
            file_obs = path_obs + '/output_' + datestr + '.npz'
            file_obserr = path_obs + '/output_realerror_' + datestr + '.npz'

            # load background data (value and error)
            datatemp = np.load(file_bac)
            v_bac = datatemp['merge_data']
            if var == 'tmean' or var == 'trange':
                e_bac = datatemp['merge_error_raw']  # error in actual space
            elif var == 'prcp':
                if prcp_space == 'Actual':
                    e_bac = datatemp['merge_error_raw']
                elif prcp_space == 'Gaussian':
                    if weightmode == 'BMA':
                        e_bac = datatemp['merge_error_bc']
                        v_bac = box_cox_transform(v_bac)
                    elif weightmode == 'RMSE':
                        e_bac = datatemp['merge_error_raw']
                        truth = v_bac - e_bac
                        v_bac = box_cox_transform(v_bac)
                        e_bac = v_bac - box_cox_transform(truth)
            else:
                sys.exit('Unknown variable')
            del datatemp

            # load observation data (value and error)
            datatemp = np.load(file_obs)
            datatemp2 = np.load(file_obserr)
            if var == 'tmean' or var == 'trange':
                v_obs = datatemp[var]
                # e_obs = datatemp[var + '_err']
                e_obs = datatemp2[var + '_realerr']
            elif var == 'prcp':
                if prcp_space == 'Actual':
                    v_obs = datatemp['pcp_raw']
                    # e_obs = datatemp['pcp_err_raw']
                    e_obs = datatemp2['pcp_realerr_raw']
                elif prcp_space == 'Gaussian':
                    v_obs = datatemp['pcp_bc']
                    # e_obs = datatemp['pcp_err_bc']
                    e_obs = datatemp['pcp_realerr_bc']
            else:
                sys.exit('Unknown variable')
            del datatemp
            v_obs = np.flipud(v_obs)
            e_obs = np.flipud(e_obs)

            ntimes = np.shape(v_bac)[2]

variable prcp


In [4]:
            # produce OI merged estimateds
            oimerge_data[var] = np.nan * np.zeros(np.shape(v_bac), dtype=np.float32)
            weightsum = np.nan * np.zeros([nrows,ncols], dtype=np.float32)
            for r in range(nrows):
                for c in range(ncols):
                    if mask[r, c] != 1:
                        continue
                    print(r,c)
                    if r < hwsize:
                        rse = [0, r + hwsize + 1]
                    elif r >= nrows - hwsize:
                        rse = [r - hwsize, nrows]
                    else:
                        rse = [r - hwsize, r + hwsize + 1]
                    if c < hwsize:
                        cse = [0, c + hwsize + 1]
                    elif c >= ncols - hwsize:
                        cse = [c - hwsize, ncols]
                    else:
                        cse = [c - hwsize, c + hwsize + 1]
                    snum = (rse[1] - rse[0]) * (cse[1] - cse[0])
                    tar_err_b = e_bac[r, c, :]
                    near_err_b = e_bac[rse[0]:rse[1], cse[0]:cse[1], :]
                    near_err_o = e_obs[rse[0]:rse[1], cse[0]:cse[1], :]
                    near_err_b = np.reshape(near_err_b, [snum, ntimes])
                    near_err_o = np.reshape(near_err_o, [snum, ntimes])
                    indnan = np.isnan(near_err_o[:, 0]) | np.isnan(near_err_b[:, 0])
                    near_err_b = near_err_b[~indnan, :]
                    near_err_o = near_err_o[~indnan, :]

                    weight = OImerge(tar_err_b, near_err_b, near_err_o)
                    diff = v_obs[rse[0]:rse[1], cse[0]:cse[1], :] - v_bac[rse[0]:rse[1], cse[0]:cse[1], :]
                    diff = np.reshape(diff, [snum, ntimes])
                    diff = diff[~indnan, :]
                    merge_est = v_bac[r, c, :]
                    for i in range(ntimes):
                        merge_est[i] = merge_est[i] + np.dot(weight, diff[:, i])

                    oimerge_data[var][r, c, :] = merge_est
                    weightsum[r,c] = np.sum(weight)

18 1053
18 1054
18 1055
18 1056
18 1057
18 1058
18 1059
18 1060
18 1061
18 1078
18 1079
18 1080
18 1081
18 1082
18 1083
18 1084
18 1092
18 1093
18 1094
18 1095
18 1096
18 1097
18 1098
18 1099
18 1100
18 1101
18 1102
18 1103
19 1025
19 1026
19 1027
19 1028
19 1029
19 1030
19 1031
19 1032
19 1033
19 1034
19 1035
19 1036
19 1037
19 1038
19 1039
19 1040
19 1041
19 1042
19 1043
19 1044
19 1045
19 1046
19 1047
19 1048
19 1049
19 1050
19 1051
19 1052
19 1053
19 1054
19 1055
19 1056
19 1057
19 1058
19 1059
19 1060
19 1061
19 1062
19 1063
19 1064
19 1067
19 1068
19 1069
19 1070
19 1071
19 1072
19 1073
19 1074
19 1075
19 1076
19 1077
19 1078
19 1079
19 1080
19 1081
19 1082
19 1083
19 1084
19 1085
19 1086
19 1087
19 1088
19 1089
19 1090
19 1091
19 1092
19 1093
19 1094
19 1095
19 1096
19 1097
19 1098
19 1099
19 1100
19 1101
19 1102
19 1103
19 1104
19 1105
19 1106
19 1107
19 1108
19 1109
19 1110
19 1114
19 1115
19 1116
20 997
20 998
20 999
20 1000
20 1001
20 1002
20 1003
20 1004
20 1005
20 1006
20 

25 1029
25 1030
25 1031
25 1032
25 1033
25 1034
25 1035
25 1036
25 1037
25 1038
25 1039
25 1040
25 1041
25 1042
25 1043
25 1044
25 1045
25 1046
25 1047
25 1048
25 1049
25 1050
25 1051
25 1052
25 1053
25 1054
25 1055
25 1056
25 1057
25 1058
25 1059
25 1060
25 1061
25 1062
25 1063
25 1064
25 1065
25 1066
25 1067
25 1068
25 1069
25 1070
25 1071
25 1072
25 1073
25 1074
25 1075
25 1076
25 1077
25 1078
25 1079
25 1080
25 1081
25 1082
25 1083
25 1084
25 1085
25 1086
25 1087
25 1088
25 1089
25 1090
25 1091
25 1092
25 1093
25 1094
25 1095
25 1096
25 1097
25 1098
25 1099
25 1100
25 1101
25 1102
25 1103
25 1104
25 1105
25 1106
25 1107
25 1108
25 1109
25 1110
25 1111
25 1112
25 1113
25 1114
25 1115
25 1116
25 1117
25 1118
25 1119
25 1120
25 1121
25 1122
25 1123
25 1124
25 1125
25 1126
25 1127
25 1128
25 1129
25 1130
25 1131
25 1132
25 1133
25 1134
25 1135
25 1136
25 1137
25 1138
25 1139
25 1140
25 1141
25 1142
25 1143
25 1144
25 1145
25 1146
25 1147
25 1148
25 1149
25 1150
25 1151
25 1152
25 1153


29 1111
29 1112
29 1113
29 1114
29 1115
29 1116
29 1117
29 1118
29 1119
29 1120
29 1121
29 1122
29 1123
29 1124
29 1125
29 1126
29 1127
29 1128
29 1129
29 1130
29 1131
29 1132
29 1133
29 1134
29 1135
29 1136
29 1137
29 1138
29 1139
29 1140
29 1141
29 1142
29 1143
29 1144
29 1145
29 1146
29 1147
29 1148
29 1149
29 1150
29 1151
29 1152
29 1153
29 1154
29 1155
29 1156
29 1157
29 1158
29 1159
29 1160
29 1161
29 1162
29 1163
29 1164
29 1165
29 1166
29 1167
29 1168
29 1169
29 1170
29 1171
29 1172
29 1173
29 1174
29 1175
29 1176
29 1177
29 1178
29 1179
29 1180
29 1181
30 892
30 893
30 894
30 895
30 897
30 898
30 899
30 900
30 901
30 902
30 903
30 904
30 905
30 906
30 907
30 908
30 909
30 910
30 911
30 912
30 913
30 914
30 915
30 916
30 917
30 918
30 919
30 920
30 921
30 922
30 923
30 924
30 925
30 926
30 927
30 928
30 929
30 930
30 931
30 932
30 933
30 934
30 935
30 936
30 937
30 938
30 939
30 940
30 941
30 942
30 943
30 944
30 945
30 946
30 947
30 948
30 949
30 950
30 951
30 952
30 953
30 95

33 1078
33 1079
33 1080
33 1081
33 1082
33 1083
33 1084
33 1085
33 1086
33 1087
33 1088
33 1089
33 1090
33 1091
33 1092
33 1093
33 1094
33 1095
33 1096
33 1097
33 1098
33 1099
33 1100
33 1101
33 1102
33 1103
33 1104
33 1105
33 1106
33 1107
33 1108
33 1109
33 1110
33 1111
33 1112
33 1113
33 1114
33 1115
33 1116
33 1117
33 1118
33 1119
33 1120
33 1121
33 1122
33 1123
33 1124
33 1125
33 1126
33 1127
33 1128
33 1129
33 1130
33 1131
33 1132
33 1133
33 1134
33 1135
33 1136
33 1137
33 1138
33 1139
33 1140
33 1141
33 1142
33 1143
33 1144
33 1145
33 1146
33 1147
33 1148
33 1149
33 1150
33 1151
34 880
34 881
34 882
34 883
34 884
34 885
34 886
34 887
34 888
34 889
34 890
34 895
34 896
34 897
34 898
34 899
34 900
34 901
34 902
34 903
34 904
34 905
34 906
34 907
34 908
34 909
34 910
34 911
34 912
34 913
34 914
34 915
34 916
34 917
34 918
34 919
34 920
34 921
34 922
34 923
34 924
34 925
34 926
34 927
34 928
34 929
34 930
34 931
34 932
34 933
34 934
34 935
34 936
34 937
34 938
34 939
34 940
34 941
34

37 1085
37 1086
37 1087
37 1088
37 1089
37 1090
37 1091
37 1092
37 1093
37 1094
37 1095
37 1096
37 1097
37 1098
37 1099
37 1100
37 1101
37 1102
37 1103
37 1104
37 1105
37 1106
37 1107
37 1108
37 1109
37 1110
37 1111
37 1112
37 1113
37 1114
37 1115
37 1116
37 1117
37 1118
37 1119
37 1120
37 1121
37 1122
37 1123
37 1124
37 1125
37 1126
37 1127
37 1128
37 1129
37 1130
37 1131
37 1132
37 1133
37 1134
37 1135
37 1136
37 1137
37 1138
37 1139
37 1140
37 1141
37 1142
37 1143
37 1144
37 1145
37 1146
37 1147
37 1148
38 856
38 857
38 858
38 861
38 862
38 863
38 864
38 865
38 867
38 868
38 869
38 870
38 871
38 872
38 873
38 874
38 875
38 876
38 877
38 878
38 879
38 880
38 881
38 882
38 897
38 898
38 899
38 900
38 901
38 902
38 903
38 904
38 905
38 906
38 907
38 908
38 909
38 910
38 911
38 912
38 913
38 914
38 915
38 916
38 917
38 918
38 919
38 920
38 921
38 922
38 923
38 924
38 925
38 926
38 927
38 928
38 929
38 930
38 931
38 932
38 933
38 934
38 935
38 936
38 937
38 938
38 939
38 940
38 941
38 94

...

688 889
688 890
688 891
688 892
688 893
688 894
688 895
688 896
688 897
688 898
688 899
688 900
688 901
688 902
688 903
688 904
688 905
688 906
688 907
688 908
688 909
688 910
688 911
688 912
688 913
688 914
688 917
688 930
688 931
688 1182
688 1183
688 1184
688 1185
688 1188
689 820
689 821
689 822
689 823
689 824
689 825
689 826
689 827
689 828
689 829
689 830
689 831
689 832
689 833
689 834
689 835
689 836
689 837
689 838
689 839
689 840
689 841
689 842
689 843
689 844
689 845
689 846
689 857
689 858
689 859
689 860
689 861
689 862
689 863
689 864
689 865
689 866
689 867
689 868
689 869
689 870
689 871
689 872
689 873
689 874
689 875
689 876
689 877
689 878
689 879
689 880
689 881
689 882
689 883
689 884
689 885
689 886
689 887
689 888
689 889
689 890
689 891
689 892
689 893
689 894
689 895
689 896
689 897
689 898
689 899
689 900
689 901
689 902
689 903
689 904
689 905
689 906
689 907
689 908
689 909
689 910
689 911
689 930
689 931
689 939
689 940
689 941
689 966
689 1182
689 1183
6

699 903
699 904
699 905
699 906
699 907
699 908
699 909
699 910
699 911
699 912
699 913
699 914
699 915
699 916
699 917
699 918
699 919
699 920
699 921
699 922
699 923
699 924
699 925
699 926
699 927
699 928
699 929
699 930
699 931
699 932
699 933
699 934
699 935
699 936
699 937
699 938
699 939
699 940
699 941
699 942
699 943
699 944
699 945
699 946
699 947
699 948
699 949
699 950
699 951
699 952
699 953
699 954
699 955
699 956
699 957
699 958
699 959
699 960
699 961
699 962
699 963
699 964
699 965
699 966
699 967
699 968
699 973
700 872
700 873
700 874
700 875
700 876
700 877
700 878
700 879
700 880
700 881
700 882
700 883
700 884
700 885
700 886
700 887
700 888
700 889
700 890
700 891
700 892
700 893
700 894
700 895
700 896
700 897
700 898
700 899
700 900
700 901
700 902
700 903
700 904
700 905
700 906
700 907
700 908
700 909
700 910
700 911
700 912
700 913
700 914
700 915
700 916
700 917
700 918
700 919
700 920
700 921
700 922
700 923
700 924
700 925
700 926
700 927
700 928
700 929


710 942
710 943
710 944
710 945
710 946
710 947
710 948
710 949
710 950
710 951
710 952
710 953
710 954
710 955
710 956
710 957
710 958
710 959
710 960
710 961
710 962
710 963
710 964
710 965
710 1189
710 1190
710 1191
711 894
711 895
711 896
711 897
711 898
711 899
711 900
711 901
711 902
711 903
711 904
711 905
711 906
711 907
711 908
711 909
711 910
711 911
711 912
711 913
711 914
711 915
711 916
711 917
711 918
711 919
711 920
711 921
711 922
711 923
711 924
711 925
711 926
711 927
711 928
711 929
711 930
711 931
711 932
711 933
711 934
711 935
711 936
711 937
711 938
711 939
711 940
711 941
711 942
711 943
711 944
711 945
711 946
711 947
711 948
711 949
711 950
711 951
711 952
711 953
711 954
711 955
711 956
711 957
711 958
711 959
711 960
711 961
711 962
711 963
711 964
711 965
711 1189
711 1190
711 1191
712 897
712 898
712 899
712 900
712 901
712 902
712 903
712 904
712 905
712 906
712 907
712 908
712 909
712 910
712 911
712 912
712 913
712 914
712 915
712 916
712 917
712 918
71

732 959
732 960
732 961
732 962
732 963
733 935
733 936
733 937
733 938
733 939
733 940
733 941
733 942
733 943
733 944
733 945
733 946
733 947
733 948
733 949
733 950
733 951
733 952
733 953
733 954
733 955
733 956
733 957
733 958
733 959
733 960
733 961
733 962
733 963
734 937
734 938
734 939
734 940
734 941
734 942
734 943
734 944
734 945
734 946
734 947
734 948
734 949
734 950
734 951
734 952
734 953
734 954
734 955
734 956
734 957
734 958
734 959
734 960
734 961
734 962
734 963
735 938
735 939
735 940
735 941
735 942
735 943
735 944
735 945
735 946
735 947
735 948
735 949
735 950
735 951
735 952
735 953
735 954
735 955
735 956
735 957
735 958
735 959
735 960
735 961
735 962
736 939
736 940
736 941
736 942
736 943
736 944
736 945
736 946
736 947
736 948
736 949
736 950
736 951
736 952
736 953
736 954
736 955
736 956
736 957
736 958
736 959
736 960
736 961
737 940
737 941
737 942
737 943
737 944
737 945
737 946
737 947
737 948
737 949
737 950
737 951
737 952
737 953
737 954
737 955


764 964
764 965
764 966
764 967
764 968
764 969
764 970
764 971
764 972
764 973
764 974
764 975
764 976
764 977
764 978
764 979
764 980
764 981
764 982
764 983
764 984
764 985
764 986
764 987
764 988
764 989
764 990
764 991
764 992
764 993
764 994
764 995
764 996
764 997
764 998
764 999
764 1000
764 1001
764 1002
764 1003
764 1004
764 1009
764 1014
764 1015
764 1016
764 1017
764 1018
764 1019
764 1020
764 1021
764 1022
764 1023
764 1024
764 1025
764 1026
764 1027
765 963
765 964
765 965
765 966
765 967
765 968
765 969
765 970
765 971
765 972
765 973
765 974
765 975
765 976
765 977
765 978
765 979
765 980
765 981
765 982
765 983
765 984
765 985
765 986
765 987
765 988
765 989
765 990
765 991
765 992
765 993
765 994
765 995
765 996
765 997
765 998
765 999
765 1000
765 1008
765 1009
765 1010
765 1011
765 1014
765 1015
765 1016
765 1017
765 1018
765 1019
765 1020
765 1021
765 1022
765 1023
765 1024
765 1025
765 1026
765 1027
765 1028
766 966
766 967
766 968
766 969
766 970
766 971
766 972


In [61]:
mm=np.zeros([ntimes,3])
for i in range(ntimes):
    mm[i,0]=np.nanmean(v_obs[:,:,i])
    mm[i,1]=np.nanmean(v_bac[:,:,i])
    mm[i,2]=np.nanmean(oimerge_data[var][:,:,i])
mm

array([[0.9386912 , 0.72664881, 0.89727098],
       [1.00228608, 0.67912841, 0.92015636],
       [0.88599914, 0.74267054, 0.86155748],
       [1.43856966, 0.94984293, 1.31461227],
       [1.33596647, 1.09977412, 1.30003285],
       [1.02362752, 0.77404577, 0.96383166],
       [1.11221325, 0.89959693, 1.06232262],
       [1.02694654, 0.72927147, 0.945858  ],
       [1.23706985, 1.04676795, 1.20060873],
       [1.54218924, 1.32643366, 1.50184023],
       [3.27090001, 2.86680961, 3.19858909],
       [3.20899534, 2.82489777, 3.14064527],
       [1.98958862, 1.89201438, 2.00118399],
       [1.98816812, 1.6455822 , 1.9117893 ],
       [1.35107863, 1.01262832, 1.25497782],
       [1.3076036 , 1.12741506, 1.27104878],
       [2.04006457, 1.6229558 , 1.93550396],
       [2.21058226, 1.899248  , 2.14876056],
       [1.66977596, 1.3918792 , 1.62317014],
       [1.14620018, 1.00485981, 1.13149142],
       [1.74865568, 1.26521075, 1.62914932],
       [2.4029355 , 2.08851004, 2.33366299],
       [2.

In [60]:
v_obs[v_obs<0]=np.nan